In [1]:
import glob
import json
import pandas as pd
from fuzzywuzzy import fuzz 

In [2]:
json_files = glob.glob('../data/google_places_results/results_*.json')

In [3]:
def process_json_file(filename):
    with open(filename) as result_file:
        results_json = json.load(result_file)
        results_json_list = []
        for result_json in results_json:
            for result_json_result in result_json['results']:
                result_json_result['orig_mapped_location'] = result_json['mapped_location']
                result_json_result['orig_address'] = result_json['address']
                results_json_list.append(result_json_result)
        return pd.DataFrame(results_json_list)

In [4]:
frames = [process_json_file(file_path) for file_path in json_files]

In [5]:
all_places_results = pd.concat(frames)

In [6]:
all_places_results.head(2)

business_status                                           geometry  \
0     OPERATIONAL  {'location': {'lat': 36.148618, 'lng': -86.807...   
1     OPERATIONAL  {'location': {'lat': 36.1484482, 'lng': -86.80...   

                                                icon  \
0  https://maps.gstatic.com/mapfiles/place_api/ic...   
1  https://maps.gstatic.com/mapfiles/place_api/ic...   

                       name       opening_hours  \
0  Martin's Bar-B-Que Joint  {'open_now': True}   
1                 lunescent                 NaN   

                                              photos  \
0  [{'height': 5354, 'html_attributions': ['<a hr...   
1                                                NaN   

                      place_id  \
0  ChIJ5V0NuYJnZIgRCqjZMw9qlfs   
1  ChIJT3mJkbtmZIgRnJSG4TiY8yk   

                                           plus_code  price_level  rating  \
0  {'compound_code': '45XV+C3 Nashville, TN, USA'...          2.0     4.4   
1  {'compound_code': '45XR+9W Nashville, TN, USA'...          NaN     5.0   

                     reference   scope  \
0  ChIJ5V0NuYJnZIgRCqjZMw9qlfs  GOOGLE   
1  ChIJT3mJkbtmZIgRnJSG4TiY8yk  GOOGLE   

                                               types  user_ratings_total  \
0  [restaurant, food, point_of_interest, establis...               783.0   
1           [food, point_of_interest, establishment]                 3.0   

                          vicinity             orig_mapped_location  \
0   2400 Elliston Place, Nashville  (36.148664, -86.80740139999999)   
1  216 Reidhurst Avenue, Nashville  (36.148664, -86.80740139999999)   

                  orig_address permanently_closed  
0  2400 Elliston Pl, Nashville                NaN  
1  2400 Elliston Pl, Nashville                NaN

In [14]:
def matcher(column1, column2):
    names_array=[]
    ratio_array=[]    
    if column1 in column2:
        return 100
    else:   
        return fuzz.partial_ratio(column1,column2)

In [18]:
all_places_results['match_ratio'] = all_places_results.apply(
    lambda x: matcher(x['vicinity'].split(',')[0], x['orig_address'].split(',')[0]), axis=1)

In [32]:
all_places_results.head()

business_status                                           geometry  \
0     OPERATIONAL  {'location': {'lat': 36.148618, 'lng': -86.807...   
1     OPERATIONAL  {'location': {'lat': 36.1484482, 'lng': -86.80...   
2     OPERATIONAL  {'location': {'lat': 36.14815, 'lng': -86.8071...   
3     OPERATIONAL  {'location': {'lat': 36.1483514, 'lng': -86.80...   
4     OPERATIONAL  {'location': {'lat': 36.1482875, 'lng': -86.80...   

                                                icon  \
0  https://maps.gstatic.com/mapfiles/place_api/ic...   
1  https://maps.gstatic.com/mapfiles/place_api/ic...   
2  https://maps.gstatic.com/mapfiles/place_api/ic...   
3  https://maps.gstatic.com/mapfiles/place_api/ic...   
4  https://maps.gstatic.com/mapfiles/place_api/ic...   

                       name       opening_hours  \
0  Martin's Bar-B-Que Joint  {'open_now': True}   
1                 lunescent                 NaN   
2                 Music row                 NaN   
3                Syntel Inc                 NaN   
4        Nicholson Cleaners  {'open_now': True}   

                                              photos  \
0  [{'height': 5354, 'html_attributions': ['<a hr...   
1                                                NaN   
2                                                NaN   
3                                                NaN   
4  [{'height': 1536, 'html_attributions': ['<a hr...   

                      place_id  \
0  ChIJ5V0NuYJnZIgRCqjZMw9qlfs   
1  ChIJT3mJkbtmZIgRnJSG4TiY8yk   
2  ChIJy_aEQxVnZIgRWFCq1zfFfp0   
3  ChIJmz2llrtmZIgRfwVcJAVjB4U   
4  ChIJpbSNjrtmZIgRyF_x9SbRk0M   

                                           plus_code  price_level  rating  \
0  {'compound_code': '45XV+C3 Nashville, TN, USA'...          2.0     4.4   
1  {'compound_code': '45XR+9W Nashville, TN, USA'...          NaN     5.0   
2  {'compound_code': '45XV+74 Nashville, TN, USA'...          NaN     NaN   
3  {'compound_code': '45XR+8R Nashville, TN, USA'...          NaN     NaN   
4  {'compound_code': '45XR+8R Nashville, TN, USA'...          NaN     4.2   

                     reference   scope  \
0  ChIJ5V0NuYJnZIgRCqjZMw9qlfs  GOOGLE   
1  ChIJT3mJkbtmZIgRnJSG4TiY8yk  GOOGLE   
2  ChIJy_aEQxVnZIgRWFCq1zfFfp0  GOOGLE   
3  ChIJmz2llrtmZIgRfwVcJAVjB4U  GOOGLE   
4  ChIJpbSNjrtmZIgRyF_x9SbRk0M  GOOGLE   

                                               types  user_ratings_total  \
0  [restaurant, food, point_of_interest, establis...               783.0   
1           [food, point_of_interest, establishment]                 3.0   
2  [electronics_store, home_goods_store, point_of...                 NaN   
3                 [point_of_interest, establishment]                 NaN   
4        [laundry, point_of_interest, establishment]                15.0   

                                vicinity             orig_mapped_location  \
0         2400 Elliston Place, Nashville  (36.148664, -86.80740139999999)   
1        216 Reidhurst Avenue, Nashville  (36.148664, -86.80740139999999)   
2        2400 West End Avenue, Nashville  (36.148664, -86.80740139999999)   
3  205 Reidhurst Avenue # 200, Nashville  (36.148664, -86.80740139999999)   
4         2410 Elliston Place, Nashville  (36.148664, -86.80740139999999)   

                  orig_address permanently_closed  match_ratio  
0  2400 Elliston Pl, Nashville                NaN          100  
1  2400 Elliston Pl, Nashville                NaN           38  
2  2400 Elliston Pl, Nashville                NaN           56  
3  2400 Elliston Pl, Nashville                NaN           44  
4  2400 Elliston Pl, Nashville                NaN           94

In [31]:
for addr, grp in all_places_results[all_places_results['match_ratio'] > 93].groupby('orig_address'):
    print(addr)
    print(grp[grp.match_ratio == grp.match_ratio.max()].iloc[0])
    print('='*30)

1 Averitt Express Dr, Nashville
business_status                                               OPERATIONAL
geometry                {'location': {'lat': 36.109046, 'lng': -86.717...
icon                    https://maps.gstatic.com/mapfiles/place_api/ic...
name                                   Averitt Express: On Tour Logistics
opening_hours                                          {'open_now': True}
photos                  [{'height': 608, 'html_attributions': ['<a hre...
place_id                                      ChIJjQb-7xVvZIgRS5fRFwn2AEk
plus_code               {'compound_code': '475M+J4 Nashville, TN, USA'...
price_level                                                           NaN
rating                                                                4.3
reference                                     ChIJjQb-7xVvZIgRS5fRFwn2AEk
scope                                                              GOOGLE
types                                  [point_of_interest, establishment]
user_r

Name: 25, dtype: object
1030 Visco Dr, Nashville
business_status                                               OPERATIONAL
geometry                {'location': {'lat': 36.1605984, 'lng': -86.73...
icon                    https://maps.gstatic.com/mapfiles/place_api/ic...
name                                                 Pine Bluff Materials
opening_hours                                          {'open_now': True}
photos                  [{'height': 2988, 'html_attributions': ['<a hr...
place_id                                      ChIJPxRcUZxoZIgRA-2V7Aj3Z1I
plus_code               {'compound_code': '5766+63 Nashville, TN, USA'...
price_level                                                           NaN
rating                                                                4.3
reference                                     ChIJPxRcUZxoZIgRA-2V7Aj3Z1I
scope                                                              GOOGLE
types                                  [point_of_interest, esta

Name: 355, dtype: object
1119 Halcyon Ave, Nashville
business_status                                               OPERATIONAL
geometry                {'location': {'lat': 36.12242930000001, 'lng':...
icon                    https://maps.gstatic.com/mapfiles/place_api/ic...
name                                                 M L Crawford's Salon
opening_hours                                          {'open_now': True}
photos                  [{'height': 4032, 'html_attributions': ['<a hr...
place_id                                      ChIJKSRnKDBkZIgRNiUGCK_u6Hc
plus_code               {'compound_code': '46C6+X2 Nashville, TN, USA'...
price_level                                                           NaN
rating                                                                4.5
reference                                     ChIJKSRnKDBkZIgRNiUGCK_u6Hc
scope                                                              GOOGLE
types                    [beauty_salon, point_of_interest, 

Name: 445, dtype: object
1213 Dickerson Rd, Goodlettsville
business_status                                               OPERATIONAL
geometry                {'location': {'lat': 36.29447090000001, 'lng':...
icon                    https://maps.gstatic.com/mapfiles/place_api/ic...
name                                                         FedEx OnSite
opening_hours                                          {'open_now': True}
photos                  [{'height': 499, 'html_attributions': ['<a hre...
place_id                                      ChIJKY5LEAFDZIgRGIyDczs0vLA
plus_code               {'compound_code': '77V9+QM Goodlettsville, TN,...
price_level                                                           NaN
rating                                                                NaN
reference                                     ChIJKY5LEAFDZIgRGIyDczs0vLA
scope                                                              GOOGLE
types                                  [point_of_inte

Name: 110, dtype: object
1400 Antioch Pike, Antioch
business_status                                               OPERATIONAL
geometry                {'location': {'lat': 36.083567, 'lng': -86.688...
icon                    https://maps.gstatic.com/mapfiles/place_api/ic...
name                                       Las Palmas Mexican Restaurante
opening_hours                                          {'open_now': True}
photos                  [{'height': 1365, 'html_attributions': ['<a hr...
place_id                                      ChIJ__8voVluZIgRP1hkyYPmaoo
plus_code               {'compound_code': '38M6+CG Nashville, TN, USA'...
price_level                                                             1
rating                                                                4.3
reference                                     ChIJ__8voVluZIgRP1hkyYPmaoo
scope                                                              GOOGLE
types                   [restaurant, food, point_of_interest

...

Name: 50, dtype: object
6838 Charlotte Pike, Nashville
business_status                                               OPERATIONAL
geometry                {'location': {'lat': 36.132815, 'lng': -86.894...
icon                    https://maps.gstatic.com/mapfiles/place_api/ic...
name                                               Chipotle Mexican Grill
opening_hours                                          {'open_now': True}
photos                  [{'height': 3024, 'html_attributions': ['<a hr...
place_id                                      ChIJ3VP4CwNiZIgRrbsS04Nc4_0
plus_code               {'compound_code': '44M4+47 Nashville, TN, USA'...
price_level                                                             1
rating                                                                4.1
reference                                     ChIJ3VP4CwNiZIgRrbsS04Nc4_0
scope                                                              GOOGLE
types                   [restaurant, food, point_of_inter

Name: 490, dtype: object
7220 Charlotte Pike, Nashville
business_status                                               OPERATIONAL
geometry                {'location': {'lat': 36.1235894, 'lng': -86.91...
icon                    https://maps.gstatic.com/mapfiles/place_api/ic...
name                                                        VFW Post 1970
opening_hours                                          {'open_now': True}
photos                  [{'height': 4032, 'html_attributions': ['<a hr...
place_id                                      ChIJ7aeWeeWJZIgR2tmU1uD5Hyg
plus_code               {'compound_code': '43FP+CW Nashville, TN, USA'...
price_level                                                           NaN
rating                                                                4.6
reference                                     ChIJ7aeWeeWJZIgR2tmU1uD5Hyg
scope                                                              GOOGLE
types                                  [point_of_interes

Name: 450, dtype: object
8100 Tridon Dr, Nan
business_status                                               OPERATIONAL
geometry                {'location': {'lat': 35.9321517, 'lng': -86.52...
icon                    https://maps.gstatic.com/mapfiles/place_api/ic...
name                                             Ideal Clamp Products Inc
opening_hours                                                         NaN
photos                                                                NaN
place_id                                      ChIJ49BLspULZIgRUIhUEuV3P9I
plus_code               {'compound_code': 'WFJF+VF Smyrna, TN, USA', '...
price_level                                                           NaN
rating                                                                2.8
reference                                     ChIJ49BLspULZIgRUIhUEuV3P9I
scope                                                              GOOGLE
types                                  [point_of_interest, establis

Name: 70, dtype: object
901 Broadway, Nashville
business_status                                               OPERATIONAL
geometry                {'location': {'lat': 36.157937, 'lng': -86.783...
icon                    https://maps.gstatic.com/mapfiles/place_api/ic...
name                                              Nashville Web Solutions
opening_hours                                          {'open_now': True}
photos                                                                NaN
place_id                                      ChIJ_3v8qfVmZIgRxPy-ivLmpAc
plus_code               {'compound_code': '5658+5J Nashville, TN, USA'...
price_level                                                           NaN
rating                                                                  5
reference                                     ChIJ_3v8qfVmZIgRxPy-ivLmpAc
scope                                                              GOOGLE
types                                  [point_of_interest, estab

Name: 200, dtype: object
Gallatin Pike, Nashville
business_status                                               OPERATIONAL
geometry                {'location': {'lat': 36.2147408, 'lng': -86.73...
icon                    https://maps.gstatic.com/mapfiles/place_api/ic...
name                                                   Craddock For Mayor
opening_hours                                                         NaN
photos                                                                NaN
place_id                                      ChIJpZGgyBxoZIgRJcur0873HQw
plus_code               {'compound_code': '6779+VP Nashville, TN, USA'...
price_level                                                           NaN
rating                                                                NaN
reference                                     ChIJpZGgyBxoZIgRJcur0873HQw
scope                                                              GOOGLE
types                   [local_government_office, point_of_int